In [1]:
!git clone https://github.com/facebookresearch/pifuhd

Cloning into 'pifuhd'...
remote: Enumerating objects: 222, done.
remote: Counting objects: 100% (126/126), done.
remote: Compressing objects: 100% (44/44), done.
remote: Total 222 (delta 92), reused 82 (delta 82), pack-reused 96
Receiving objects: 100% (222/222), 399.39 KiB | 4.16 MiB/s, done.
Resolving deltas: 100% (114/114), done.


In [2]:
cd /content/pifuhd/sample_images

/content/pifuhd/sample_images


In [3]:
from google.colab import files
import io

# Upload the file
uploaded_files = files.upload()

# Get the filename
filename = list(uploaded_files.keys())[0]

# Get the content of the uploaded file as bytes
file_content = uploaded_files[filename]

# Define the path where you want to save the file
local_path = "/content/" + filename  # You can change this path as per your requirement

# Write the content to a local file
with open(local_path, "wb") as f:
    f.write(file_content)

print("File saved at:", local_path)


Saving manhalf.jpg to manhalf.jpg
File saved at: /content/manhalf.jpg


In [4]:
!pip install rembg

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.8/6.8 MB 26.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.0/53.0 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 13.3 MB/s eta 0:00:00


In [6]:
from rembg import remove
from PIL import Image
output_path = '/content/output.png'
input= Image.open(local_path)
output = remove(input)
output.save(output_path)

In [7]:
import os


# image_path = '/content/cut.jpg'

image_dir = os.path.dirname(output_path)
file_name = os.path.splitext(os.path.basename(output_path))[0]


obj_path = '/content/pifuhd/results/pifuhd_final/recon/result_%s_256.obj' % file_name
out_img_path = '/content/pifuhd/results/pifuhd_final/recon/result_%s_256.png' % file_name
video_path = '/content/pifuhd/results/pifuhd_final/recon/result_%s_256.mp4' % file_name
video_display_path = '/content/pifuhd/results/pifuhd_final/result_%s_256_display.mp4' % file_name

In [8]:
cd /content

/content


In [9]:
# obj_path

In [10]:
!git clone https://github.com/Daniil-Osokin/lightweight-human-pose-estimation.pytorch.git

Cloning into 'lightweight-human-pose-estimation.pytorch'...
remote: Enumerating objects: 123, done.
remote: Counting objects: 100% (33/33), done.
remote: Compressing objects: 100% (14/14), done.
remote: Total 123 (delta 20), reused 20 (delta 19), pack-reused 90
Receiving objects: 100% (123/123), 229.49 KiB | 2.94 MiB/s, done.
Resolving deltas: 100% (52/52), done.


In [11]:
cd /content/lightweight-human-pose-estimation.pytorch/

/content/lightweight-human-pose-estimation.pytorch


In [12]:
!wget https://download.01.org/opencv/openvino_training_extensions/models/human_pose_estimation/checkpoint_iter_370000.pth

--2024-04-17 09:31:20--  https://download.01.org/opencv/openvino_training_extensions/models/human_pose_estimation/checkpoint_iter_370000.pth
Resolving download.01.org (download.01.org)... 23.10.199.19, 2600:1407:3c00:158f::a87, 2600:1407:3c00:158b::a87
Connecting to download.01.org (download.01.org)|23.10.199.19|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 87959810 (84M) [application/octet-stream]
Saving to: ‘checkpoint_iter_370000.pth’

checkpoint_iter_370 100%[===================>]  83.88M   172MB/s    in 0.5s    

2024-04-17 09:31:21 (172 MB/s) - ‘checkpoint_iter_370000.pth’ saved [87959810/87959810]



In [13]:
import torch
import cv2
import numpy as np
from models.with_mobilenet import PoseEstimationWithMobileNet
from modules.keypoints import extract_keypoints, group_keypoints
from modules.load_state import load_state
from modules.pose import Pose, track_poses
import demo

def get_rect(net, images, height_size):
    net = net.eval()

    stride = 8
    upsample_ratio = 4
    num_keypoints = Pose.num_kpts
    previous_poses = []
    delay = 33
    for image in images:
        rect_path = image.replace('.%s' % (image.split('.')[-1]), '_rect.txt')
        img = cv2.imread(image, cv2.IMREAD_COLOR)
        orig_img = img.copy()
        orig_img = img.copy()
        heatmaps, pafs, scale, pad = demo.infer_fast(net, img, height_size, stride, upsample_ratio, cpu=False)

        total_keypoints_num = 0
        all_keypoints_by_type = []
        for kpt_idx in range(num_keypoints):  # 19th for bg
            total_keypoints_num += extract_keypoints(heatmaps[:, :, kpt_idx], all_keypoints_by_type, total_keypoints_num)

        pose_entries, all_keypoints = group_keypoints(all_keypoints_by_type, pafs)
        for kpt_id in range(all_keypoints.shape[0]):
            all_keypoints[kpt_id, 0] = (all_keypoints[kpt_id, 0] * stride / upsample_ratio - pad[1]) / scale
            all_keypoints[kpt_id, 1] = (all_keypoints[kpt_id, 1] * stride / upsample_ratio - pad[0]) / scale
        current_poses = []

        rects = []
        for n in range(len(pose_entries)):
            if len(pose_entries[n]) == 0:
                continue
            pose_keypoints = np.ones((num_keypoints, 2), dtype=int) * -1
            valid_keypoints = []
            for kpt_id in range(num_keypoints):
                if pose_entries[n][kpt_id] != -1.0:  # keypoint was found
                    pose_keypoints[kpt_id, 0] = int(all_keypoints[int(pose_entries[n][kpt_id]), 0])
                    pose_keypoints[kpt_id, 1] = int(all_keypoints[int(pose_entries[n][kpt_id]), 1])
                    valid_keypoints.append([pose_keypoints[kpt_id, 0], pose_keypoints[kpt_id, 1]])
            valid_keypoints = np.array(valid_keypoints)

            if pose_entries[n][10] != -1.0 or pose_entries[n][13] != -1.0:
              pmin = valid_keypoints.min(0)
              pmax = valid_keypoints.max(0)

              center = (0.5 * (pmax[:2] + pmin[:2])).astype(int)
              radius = int(0.65 * max(pmax[0]-pmin[0], pmax[1]-pmin[1]))
            elif pose_entries[n][10] == -1.0 and pose_entries[n][13] == -1.0 and pose_entries[n][8] != -1.0 and pose_entries[n][11] != -1.0:
              # if leg is missing, use pelvis to get cropping
              center = (0.5 * (pose_keypoints[8] + pose_keypoints[11])).astype(int)
              radius = int(1.45*np.sqrt(((center[None,:] - valid_keypoints)**2).sum(1)).max(0))
              center[1] += int(0.05*radius)
            else:
              center = np.array([img.shape[1]//2,img.shape[0]//2])
              radius = max(img.shape[1]//2,img.shape[0]//2)

            x1 = center[0] - radius
            y1 = center[1] - radius

            rects.append([x1, y1, 2*radius, 2*radius])

        np.savetxt(rect_path, np.array(rects), fmt='%d')

In [14]:
net = PoseEstimationWithMobileNet().cuda()
checkpoint = torch.load('checkpoint_iter_370000.pth', map_location='cuda')
load_state(net, checkpoint)

get_rect(net, [output_path], 512)

In [15]:
cd /content/pifuhd/

/content/pifuhd


In [16]:
!sh ./scripts/download_trained_model.sh

+ mkdir -p checkpoints
+ cd checkpoints
+ wget https://dl.fbaipublicfiles.com/pifuhd/checkpoints/pifuhd.pt pifuhd.pt
--2024-04-17 09:32:02--  https://dl.fbaipublicfiles.com/pifuhd/checkpoints/pifuhd.pt
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 3.162.163.51, 3.162.163.19, 3.162.163.11, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|3.162.163.51|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1548375177 (1.4G) [application/octet-stream]
Saving to: ‘pifuhd.pt’

pifuhd.pt           100%[===================>]   1.44G   211MB/s    in 6.3s    

2024-04-17 09:32:08 (233 MB/s) - ‘pifuhd.pt’ saved [1548375177/1548375177]

--2024-04-17 09:32:08--  http://pifuhd.pt/
Resolving pifuhd.pt (pifuhd.pt)... failed: Name or service not known.
wget: unable to resolve host address ‘pifuhd.pt’
FINISHED --2024-04-17 09:32:08--
Total wall clock time: 6.5s
Downloaded: 1 files, 1.4G in 6.3s (233 MB/s)


In [18]:
!python -m apps.simple_test -r 256 --use_rect -i $image_dir

Resuming from  ./checkpoints/pifuhd.pt
test data size:  1
initialize network with normal
initialize network with normal
generate mesh (test) ...
  0% 0/1 [00:00<?, ?it/s]./results/pifuhd_final/recon/result_output_256.obj
100% 1/1 [00:07<00:00,  7.61s/it]


In [19]:
import sys
import torch
pyt_version_str=torch.__version__.split("+")[0].replace(".", "")
version_str="".join([
    f"py3{sys.version_info.minor}_cu",
    torch.version.cuda.replace(".",""),
    f"_pyt{pyt_version_str}"
])
!pip install fvcore iopath
!pip install --no-index --no-cache-dir pytorch3d -f https://dl.fbaipublicfiles.com/pytorch3d/packaging/wheels/{version_str}/download.html

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.2/50.2 kB 837.7 kB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 2.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for fvcore: filename=fvcore-0.1.5.post20221221-py3-none-any.whl size=61400 sha256=eaa6cf39cf49fe50cd32294b0e56b26a24625b170fcb10edfac634744749fc88
  Stored in directory: /root/.cache/pip/wheels/01/c0/af/77c1cf53a1be9e42a52b48e5af2169d40ec2e89f7362489dd0
  Created wheel for iopath: filename=iopath-0.1.10-py3-none-any.whl size=31532 sha256=346a278699deca47c3277d5223cca4e99e56bc100b101874cd33959de30ad9bd
  Stored in directory: /root/.cache/pip/wheels/9a/a3/b6/ac0fcd1b4ed5cfeb3db92e6a0e476cfd48ed0df92b91080c1d
Successfully built fvcore iopath
Looking in links: https://dl.fbaipublicfiles.com/pytorch3d/packaging/wheels/py310_cu121_pyt221/download.html
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.4/20.4 MB 66.4 MB/s eta 0:00:00


In [ ]:
# from lib.colab_util import generate_video_from_obj, set_renderer, video

# renderer = set_renderer()
# generate_video_from_obj(obj_path, out_img_path, video_path, renderer)

# # we cannot play a mp4 video generated by cv2
# # !ffmpeg -i $video_path -vcodec libx264 $video_display_path -y -loglevel quiet
# video(video_display_path)

In [ ]:
# ! pip install pywavefront

In [ ]:
# !pip install PyVista

In [ ]:
# # Step 1: Install PyWavefront if not already installed
# # pip install PyWavefront

# from pywavefront import Wavefront

# # Step 2: Read the OBJ file
# obj_file_path = '/content/pifuhd/results/pifuhd_final/recon/result_newbg_256.obj'
# obj = Wavefront(obj_file_path)

# # Step 3: Extract vertices and faces from the OBJ file
# vertices = np.array(obj.vertices)
# faces = obj.mesh_list[0].faces

# # Step 4: Create a mesh
# # You can use the extracted vertices and faces to create a mesh using your preferred 3D library,
# # such as PyOpenGL, PyVista, or Pythreejs.
# vertex_positions=vertices[:,:3]

# faces=np.array(faces,dtype=int)
# # Example using PyVista:
# import pyvista as pv

# mesh = pv.PolyData(vertex_positions, faces)

# # Step 5: Optionally, visualize the mesh
# mesh.plot()

# # Or save the mesh to a file
# output_file_path = '/content/pifuhd/results/pifuhd_final/recon/output_mesh.vtk'
# mesh.save(output_file_path)


In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

In [20]:
!pip install trimesh

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 693.8/693.8 kB 2.8 MB/s eta 0:00:00


In [21]:
import trimesh

# Load the OBJ file
mesh = trimesh.load(obj_path)

# Export the mesh to desired format (e.g., STL)
mesh.show()